# IMPORT

In [61]:
import os
import re
import json
import bm25s
import asyncio
import pandas as pd

from tqdm import tqdm
from googletrans import Translator

# FUNCTION

In [62]:
def bm25_retriever(query, content, k=12):
    corpus = content.split(".")

    #-- Retriever
    retriever = bm25s.BM25(corpus=corpus)
    retriever.index(bm25s.tokenize(corpus))
 
    #-- Retriever all relevant content
    results, scores = retriever.retrieve(bm25s.tokenize(query), k=min(k, len(corpus)))
    return results[0]

In [63]:
async def gg_translate(sentence, from_lang="vi", to_lang="en"):
    async with Translator() as translator:
        result = await translator.translate(sentence, src=from_lang, dest=to_lang)
        return result

async def run_gg_translate(sentence, from_lang="vi", to_lang="en"):
    translated_sentence_result = await gg_translate(sentence, from_lang=from_lang, to_lang=to_lang)
    return translated_sentence_result.text

In [64]:
def load_json(path):
    with open(path, "r", encoding="utf-8") as file:
        json_content = json.load(file)
        return json_content
    
#---- Save json
def save_json(path, content):
    with open(path, "w", encoding="utf-8") as file:
        json.dump(content, file, ensure_ascii=False, indent=3)

In [65]:
def clean_text(
        text,
        methods=['rmv_link', 'rmv_punc', 'lower', 'rmv_space'],
        custom_punctuation = '!"#$%&\'()*+,.-:;<=>?@[\\]^_/`{|}~”“',
    ):
    cleaned_text = text
    for method in methods:
        if method == 'rmv_link':
            # Remove link
            cleaned_text = re.sub('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+', '', cleaned_text)
            cleaned_text = "".join(cleaned_text)
        elif method == 'rmv_punc':
            # Remove punctuation
            cleaned_text = re.sub('[%s]' % re.escape(custom_punctuation), '' , cleaned_text)
        elif method == 'lower':
            # Lowercase
            cleaned_text = cleaned_text.lower()
        elif method == 'rmv_space':
            # Remove extra space
            cleaned_text = re.sub(' +', ' ', cleaned_text)
            cleaned_text = cleaned_text.strip()
    return cleaned_text

<>:10: SyntaxWarning: invalid escape sequence '\('
<>:10: SyntaxWarning: invalid escape sequence '\('
C:\Users\ASUS\AppData\Local\Temp\ipykernel_6360\542473805.py:10: SyntaxWarning: invalid escape sequence '\('
  cleaned_text = re.sub('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+', '', cleaned_text)


# LOAD DATA

In [66]:
contents_dir = r"F:\UNIVERSITY\Project\Sentiment-Analysis-Airflow\Financial-Sentiment-Analysis\projects\newest_crawl\save_news_contents"
all_contents_paths = [os.path.join(contents_dir, name) for name in os.listdir(contents_dir)]
all_contents_jsons = [load_json(path) for path in tqdm(all_contents_paths)]

100%|██████████| 999/999 [00:04<00:00, 248.59it/s]


In [67]:
merge_contents_json = [item for items in all_contents_jsons for item in items]

# PREPROCESSING

In [68]:
processed_merge_contents_json = []
for idx, item in tqdm(enumerate(merge_contents_json)):
    #-- Title processing
    item["title"] = clean_text(
        text=item["title"],
        custom_punctuation="#$}{!)("
    )

    #-- Date time Processing
    time = item["time"]
    posted_date = item["posted_date"]
    if "giờ trước" in time:
        continue
    posted_date = posted_date.replace("Ngày đăng", "")
    item["posted_date"] = posted_date.strip()

    #-- Content Processing
    item["main_content"] = item["main_content"].replace("Vietstock - ", "")
    item["main_content"] = item["main_content"].replace("\n", " ")
    item["main_content"] = clean_text(
        text=item["main_content"],
        custom_punctuation="#$}{!)("
    )
    item["main_content"] = item["main_content"].replace(item["title"], "")

    #-- Translate
    # item["title"] = await run_gg_translate(item["title"])
    # item["main_content"] = await run_gg_translate(item["main_content"])

    #-- BM25 Retriever
    top_k_sentences = bm25_retriever(
        query=item["title"],
        content=item["main_content"],
        k=5,
    )   
    for i, sen in enumerate(top_k_sentences):
        item[f"relative_sen_{i}"] = sen
    processed_merge_contents_json.append(item)

9988it [46:01,  3.62it/s]


In [74]:
processed_merge_contents_json

[{'title': '22/01: đọc gì trước giờ giao dịch chứng khoán?',
  'time': '22 thg 1, 2026',
  'posted_date': '06:57 22/01/2026',
  'main_content': ' cùng điểm lại những tin tức tài chính kinh tế trong nước và quốc tế đáng chú ý diễn ra trong 24h qua trước giờ giao dịch hôm nay. * cổ phiếu dsc “nằm sàn” với thanh khoản kỷ lục sau thông tin chủ tịch hđqt đăng ký bán hơn 21 triệu cp. ông nguyễn đức anh – chủ tịch hđqt ctcp chứng khoán dsc hose: dsc đã đăng ký bán hơn 21.3 triệu cp dsc trong thời gian từ 26/01-13/02/2026 nhằm mục đích thay đổi danh mục đầu tư. >>> * theo dấu dòng tiền cá mập 21/01: khối ngoại hạ nhiệt bán ròng trong ngày thị trường biến động. trong phiên vn-index giảm điểm, nhà đầu tư nước ngoài dù tiếp tục bán ròng nhưng cường độ thấp hơn phiên trước đáng kể. trong khi đó, khối tự doanh chỉ bán ròng nhẹ và giao dịch tương đối cầm chừng. >>> * vndirect tăng 36% lãi ròng quý 4 nhờ cho vay, gửi tiền và hoàn nhập dự phòng. quý 4/2025, ctcp chứng khoán vndirect hose: vnd lãi ròng

# PREPROCESSING DATAFRAME

In [75]:
data = {
    "title": [],
    "posted_date": [],
    "main_content": [],
}
for item in processed_merge_contents_json:
    for k in item.keys():
        if k not in data:
            data[k] = []
        data[k].append(item[k])
    # data["title"].append(item["title"])
    # data["posted_date"].append(item["posted_date"])
    # data["main_content"].append(item["main_content"])

In [76]:
df = pd.DataFrame(data)
df["posted_date"] = pd.to_datetime(df['posted_date'], format='%H:%M %d/%m/%Y')
df = df.sort_values(["posted_date"], ascending=True)

In [77]:
save_dir = r"F:\UNIVERSITY\Project\Sentiment-Analysis-Airflow\Financial-Sentiment-Analysis\projects\data"
df.to_csv(os.path.join(save_dir, "gather_all_contents.csv"))

In [78]:
df.head()

title         posted_date  \
9981  vietstock daily 02/12/2021: giữ vững đường mid... 2021-12-01 23:52:00   
9980        góc nhìn 02/12: quay lại ngưỡng 1,500 điểm? 2021-12-02 01:19:00   
9979      02/12: đọc gì trước giờ giao dịch chứng khoán 2021-12-02 13:00:00   
9978           cổ phiếu nào thường tăng trong tháng 12? 2021-12-02 16:00:00   
9977  nhịp đập thị trường 02/12: mở cửa tăng nhẹ dù ... 2021-12-02 16:50:00   

                                           main_content             time  \
9981   vn-index sau khi test đường middle của dải bo...  01 thg 12, 2021   
9980  bài cập nhật  một số công ty chứng khoán ctck ...  01 thg 12, 2021   
9979   cùng điểm lại những tin tức đáng chú ý về tài...  02 thg 12, 2021   
9978   vn-index trong tháng 11 đã chinh phục thành c...  02 thg 12, 2021   
9977   diễn biến bất ngờ trên sàn chứng mỹ đêm qua c...  02 thg 12, 2021   

                                         relative_sen_0  \
9981   nếu chỉ số có thể giữ vững được đường middle ...   
9980   vn-index sẽ tiếp tục tăng điểm trong phiên 02...   
9979   cùng điểm lại những tin tức đáng chú ý về tài...   
9978   trong đó, cổ phiếu của hai “ông lớn” ngành bá...   
9977   vn-index mở cửa tăng hơn 3 điểm, với lực kéo ...   

                                         relative_sen_1  \
9981   nếu chỉ số có thể giữ vững bên trên đường mid...   
9980   dự báo, trong phiên giao dịch 02/12, vn-index...   
9979   >>> * thẻ từ atm vẫn giao dịch bình thường sa...   
9978   trong khi đó tại sàn hnx, có 3 cổ phiếu luôn ...   
9977   nhóm chứng khoán rõ ràng rất nhạy cảm với mọi...   

                                         relative_sen_2  \
9981   nếu chỉ số có thể giữ vững bên trên đường mid...   
9980   dự báo trong phiên giao dịch 02/12, chỉ số vn...   
9979      51% vốn đang nắm giữ trong thời gian 02-30/12   
9978   theo dữ liệu từ vietstockfinance, tại sàn hos...   
9977   cả 2 chỉ số này đều tăng nhẹ, thậm chí hnx in...   

                                         relative_sen_3  \
9981   phân tích kỹ thuật phân tích xu hướng và dao ...   
9980   kbsv khuyến nghị nhà đầu tư chỉ kê mua lại 1 ...   
9979   >>> * khối ngoại bán ròng tháng thứ 4 liên ti...   
9978   việc có đến 3 cổ  phiếu bất động sản nằm tron...   
9977   ngược lại, 2 cổ phiếu lớn trên hose là vpb hm...   

                                         relative_sen_4  
9981   - vn-index sau khi test đường middle của dải ...  
9980   vcbs khuyến nghị nhà đầu tư tiếp tục quan sát...  
9979   >>> thị trường chứng khoán * louis holdings n...  
9978   tuy nhiên, có nhiều cổ phiếu vẫn giữ được pho...  
9977   trên nhóm này có những mã tăng đáng chú ý như...